# Healthcare Accesibility per Neighborhood in Toronto

## Introduction

Physical healthcare accesibility is defined by World Health Organization as “the availability of good health services within reasonable reach of those who need them and of opening hours, appointment systems and other aspects of service organization and delivery that allow people to obtain the services when they need them”[1]. This is an important aspect for people wellbeing and city government must guarantee access to health services to all population. For this project I will focus on estimating the accessibilty to Emergency Rooms available in Toronto, Canada.

The accurate measurement of spatial accessibility to health care is problematic chiefly because there is seldom any predetermined assignment or single pathway between individuals and specific health care services. For this project I will assume that metropolitan areas have services densely located and most individuals will access health services in close proximity. I will use the two-step floating catchment area (2SFCA) method as proposed by McGrail MR [2] and try to assess the accessibility for every neighborhood in Toronto based on the distance from neihgborhoods to hospitals and emergency rooms and the population of the neighborhoods. Also I will run the 2SFCA taking into account only the population over 65 years old which represents the 22.4% of visits to Emergency Rooms in 2015/16 and incremented the visits in 29.1% with respect to 2008/09 in Ontario [3].  

## Data

For this project I will be using foursquare API to obtain the location for the Hospitals and Emergency Rooms in Toronto, Canada. From https://open.toronto.ca/ I obtained the Neighbourhood Profiles dataset which cointains demographics data, from the 2016 Census, such as population, income, education, etc for 140 neighbourhoods. I will also use the geojson file from open toronto data and will use Open Street Map data and Pandana library to estimate the distance from the centroid of the neighbourhoods to the venues from Foursquare.

In [1]:
import pandas as pd
import numpy as np

import geopandas as gpd

import json
import requests
from pandas.io.json import json_normalize

import folium
import matplotlib.pyplot as plt
%matplotlib inline
import matplotlib.cm as cm
import matplotlib.colors as colors

from pandana.loaders import osm
from pandana.loaders import pandash5
from pandana import Network

### Census Data

In [2]:
#read census data as pandas Dataframe
toronto_census = pd.read_csv('neighbourhood-profiles-2016-csv.csv')
toronto_census.head()

_id                   Category                      Topic  \
0    1  Neighbourhood Information  Neighbourhood Information   
1    2  Neighbourhood Information  Neighbourhood Information   
2    3                 Population   Population and dwellings   
3    4                 Population   Population and dwellings   
4    5                 Population   Population and dwellings   

                      Data Source               Characteristic  \
0                 City of Toronto         Neighbourhood Number   
1                 City of Toronto         TSNS2020 Designation   
2  Census Profile 98-316-X2016001             Population, 2016   
3  Census Profile 98-316-X2016001             Population, 2011   
4  Census Profile 98-316-X2016001  Population Change 2011-2016   

  City of Toronto Agincourt North Agincourt South-Malvern West  \
0             NaN             129                          128   
1             NaN  No Designation               No Designation   
2       2,731,571          29,113                       23,757   
3       2,615,060          30,279                       21,988   
4           4.50%          -3.90%                        8.00%   

        Alderwood           Annex  ... Willowdale West  \
0              20              95  ...              37   
1  No Designation  No Designation  ...  No Designation   
2          12,054          30,526  ...          16,936   
3          11,904          29,177  ...          15,004   
4           1.30%           4.60%  ...          12.90%   

  Willowridge-Martingrove-Richview  Woburn Woodbine Corridor Woodbine-Lumsden  \
0                                7     137                64               60   
1                   No Designation     NIA    No Designation   No Designation   
2                           22,156  53,485            12,541            7,865   
3                           21,343  53,350            11,703            7,826   
4                            3.80%   0.30%             7.20%            0.50%   

         Wychwood  Yonge-Eglinton  Yonge-St.Clair York University Heights  \
0              94             100              97                      27   
1  No Designation  No Designation  No Designation                     NIA   
2          14,349          11,817          12,528                  27,593   
3          13,986          10,578          11,652                  27,713   
4           2.60%          11.70%           7.50%                  -0.40%   

       Yorkdale-Glen Park  
0                      31  
1  Emerging Neighbourhood  
2                  14,804  
3                  14,687  
4                   0.80%  

[5 rows x 146 columns]

In [3]:
#neighborhood _id in toronto_hoods is preceded by a 7 so added 7000 to _id in the density dataframe to be able to match 
hood_pop = pd.DataFrame()
hood_pop['_id'] = toronto_census.iloc[0, 6:].astype(int) + 7000
hood_pop['Population'] = toronto_census.iloc[2, 6:].str.replace(',','').astype(int)
hood_pop.head()

_id  Population
Agincourt North               7129       29113
Agincourt South-Malvern West  7128       23757
Alderwood                     7020       12054
Annex                         7095       30526
Banbury-Don Mills             7042       27695

### Geojson

In [4]:
#read geojson as pandas Dataframe
toronto_hoods = gpd.read_file('Neighbourhoods.geojson')
toronto_hoods.head()

_id   AREA_ID  AREA_ATTR_ID  PARENT_AREA_ID  AREA_SHORT_CODE  \
0  7001  25886861      25926662           49885               94   
1  7002  25886820      25926663           49885              100   
2  7003  25886834      25926664           49885               97   
3  7004  25886593      25926665           49885               27   
4  7005  25886688      25926666           49885               31   

   AREA_LONG_CODE                     AREA_NAME                     AREA_DESC  \
0              94                 Wychwood (94)                 Wychwood (94)   
1             100          Yonge-Eglinton (100)          Yonge-Eglinton (100)   
2              97           Yonge-St.Clair (97)           Yonge-St.Clair (97)   
3              27  York University Heights (27)  York University Heights (27)   
4              31       Yorkdale-Glen Park (31)       Yorkdale-Glen Park (31)   

      X     Y  LONGITUDE   LATITUDE  OBJECTID   Shape__Area  Shape__Length  \
0  None  None -79.425515  43.676919  16491505  3.217960e+06    7515.779658   
1  None  None -79.403590  43.704689  16491521  3.160334e+06    7872.021074   
2  None  None -79.397871  43.687859  16491537  2.222464e+06    8130.411276   
3  None  None -79.488883  43.765736  16491553  2.541821e+07   25632.335242   
4  None  None -79.457108  43.714672  16491569  1.156669e+07   13953.408098   

                                            geometry  
0  POLYGON ((-79.43592 43.68015, -79.43492 43.680...  
1  POLYGON ((-79.41096 43.70408, -79.40962 43.704...  
2  POLYGON ((-79.39119 43.68108, -79.39141 43.680...  
3  POLYGON ((-79.50529 43.75987, -79.50488 43.759...  
4  POLYGON ((-79.43969 43.70561, -79.44011 43.705...

### Foursquare Data

In [5]:
#fill Foursquare information
CLIENT_ID = '' # your Foursquare ID
CLIENT_SECRET = '' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

In [6]:
# Function to search venues by categories
def search_venue_by_category(names, latitudes, longitudes, categories, radius=500, limit=100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
            
        # create the API request URL for every category
        for category in categories:
            url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            limit,
            category)
            
            # make the GET request
            try:
                results = requests.get(url).json()["response"]['venues']

        # return only relevant information for each nearby venue

                venues_list.append([(
                    name, 
                    lat, 
                    lng, 
                    v['name'], 
                    v['location']['lat'], 
                    v['location']['lng'],  
                    v['categories'][0]['name']) for v in results])
            except:
                continue

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [7]:
#4bf58dd8d48988d194941735 Foursquare Venue Category for Emergency Room
toronto_er = search_venue_by_category(names=toronto_hoods['AREA_NAME'],
                                   latitudes=toronto_hoods['LATITUDE'],
                                   longitudes=toronto_hoods['LONGITUDE'], radius=5000,
                                   categories=["4bf58dd8d48988d194941735"]
                                  )

In [8]:
#toronto_er.to_csv('Emergency_Room_Toronto_4square_r10k.csv')
#toronto_er = pd.read_csv('Emergency_Room_Toronto_4square_r5000.csv')

In [9]:
print(toronto_er.shape)
toronto_er.head()

(559, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Wychwood (94)              43.676919              -79.425515   
1  Wychwood (94)              43.676919              -79.425515   
2  Wychwood (94)              43.676919              -79.425515   
3  Wychwood (94)              43.676919              -79.425515   
4  Wychwood (94)              43.676919              -79.425515   

                                     Venue  Venue Latitude  Venue Longitude  \
0                   St. Michael's Hospital       43.653784       -79.377809   
1  Toronto General Hospital Emergency Room       43.658426       -79.386462   
2         Mount Sinai Emergency Department       43.656680       -79.390283   
3                     Emergency Department       43.658314       -79.386985   
4                      Sick Kids Emergency       43.657527       -79.386513   

   Venue Category  
0        Hospital  
1  Emergency Room  
2  Emergency Room  
3  Emergency Room  
4  Emergency Room

In [10]:
toronto_er.shape

(559, 7)

In [11]:
toronto_er.drop_duplicates(subset=['Venue'], inplace=True)
toronto_er.shape

(22, 7)

In [12]:
i=0
cat = toronto_er['Venue Category'].unique()
cat_enc = {}
for x in cat:
    cat_enc[x] = i
    i += 1

In [13]:
num_cat = len(cat_enc.keys())
num_cat
cat_enc

{'Hospital': 0,
 'Emergency Room': 1,
 "Dentist's Office": 2,
 "Doctor's Office": 3,
 'Veterinarian': 4}

In [14]:
 #function to creat a choropleth_map and adding toronto_er venues as markers   
def choropleth_map(loc, geodata, data, cols, legend, zoom_start=10.8):
    Map = folium.Map(location=loc, zoom_start=zoom_start)
    Map.choropleth(geo_data=geodata,
                     data=data,
                     columns=cols,
                     name='choropleth',
                     key_on='properties._id',
                     fill_color='YlGn',
                     fill_opacity=0.7,
                     line_opacity=0.2,
                     legend_name=legend)

    # set color scheme for the clusters
    x = np.arange(num_cat)
    ys = [i + x + (i*x)**2 for i in range(num_cat)]
    colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
    rainbow = [colors.rgb2hex(i) for i in colors_array]

    # add markers to the map
    markers_colors = []
    for lat, lon, poi, cat in zip(toronto_er['Venue Latitude'], toronto_er['Venue Longitude'], toronto_er['Venue'], toronto_er['Venue Category']):
        label = folium.Popup(str(poi) + ' Category ' + str(cat), parse_html=True)
        folium.CircleMarker(
            [lat, lon],
            radius=5,
            popup=label,
            color=rainbow[cat_enc[cat]-1],
            fill=True,
            fill_color=rainbow[cat_enc[cat]-1],
            fill_opacity=0.7).add_to(Map)

    folium.LayerControl().add_to(Map)
    
    return Map

In [15]:
toronto_coord = [43.6532, -79.3832]
toronto_pop = choropleth_map(loc=toronto_coord, geodata = 'Neighbourhoods.geojson', data=hood_pop, cols=['_id', 'Population'], legend="Population per Neighborhood")

In [16]:
toronto_pop

##### Choropleth map showing population density from Toronto census data

## Method

The 2SFCA method calculates the accesibility $A_i^F$ given a population i and is defined as the sum of the supply score $R_j$ for all the supplies center in the catchment area of demand i. Following are present the equations for the two steps required:

#### First Step
Calculate supply-to-demand ratio ($R_j$) that seraches all demand locations ($k$) within threshold ($d_0$) from supply location ($j$)

### $$R_j = \frac{S_j}{\sum_{n \in (d_{kj}) \leq d_0}D_k}$$

#### Second Step
For each demand location ($i$), sum up the supply-to-demand ratios ($R_j$) that supply location ($j$) are within threshold ($d_0$) from demand location ($i$)

### $$A_i^F = \sum_{j \in (d_{ij} \leq d_0)}R_j$$


First I only keep the venues that correspond to Emergency Room and Hospital and remove neighborhood number from the Neighborhood name in toronto_hoods and toronto_er dataframes.

In [17]:
toronto_er['Venue Category'].unique()

array(['Hospital', 'Emergency Room', "Dentist's Office",
       "Doctor's Office", 'Veterinarian'], dtype=object)

In [18]:
toronto_er = toronto_er[(toronto_er['Venue Category']=='Hospital')|(toronto_er['Venue Category']=='Emergency Room')].reset_index()
toronto_er.drop('index', axis=1, inplace=True)
toronto_er.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Wychwood (94)              43.676919              -79.425515   
1  Wychwood (94)              43.676919              -79.425515   
2  Wychwood (94)              43.676919              -79.425515   
3  Wychwood (94)              43.676919              -79.425515   
4  Wychwood (94)              43.676919              -79.425515   

                                     Venue  Venue Latitude  Venue Longitude  \
0                   St. Michael's Hospital       43.653784       -79.377809   
1  Toronto General Hospital Emergency Room       43.658426       -79.386462   
2         Mount Sinai Emergency Department       43.656680       -79.390283   
3                     Emergency Department       43.658314       -79.386985   
4                      Sick Kids Emergency       43.657527       -79.386513   

   Venue Category  
0        Hospital  
1  Emergency Room  
2  Emergency Room  
3  Emergency Room  
4  Emergency Room

In [19]:
toronto_er['Neighborhood'] = toronto_er['Neighborhood'].str.extract('(.*\s\()', expand=False).str[:-2]
toronto_hoods['AREA_NAME'] = toronto_hoods['AREA_NAME'].str.extract('(.*\s\()', expand=False).str[:-2]
toronto_hoods.head()

_id   AREA_ID  AREA_ATTR_ID  PARENT_AREA_ID  AREA_SHORT_CODE  \
0  7001  25886861      25926662           49885               94   
1  7002  25886820      25926663           49885              100   
2  7003  25886834      25926664           49885               97   
3  7004  25886593      25926665           49885               27   
4  7005  25886688      25926666           49885               31   

   AREA_LONG_CODE                AREA_NAME                     AREA_DESC  \
0              94                 Wychwood                 Wychwood (94)   
1             100           Yonge-Eglinton          Yonge-Eglinton (100)   
2              97           Yonge-St.Clair           Yonge-St.Clair (97)   
3              27  York University Heights  York University Heights (27)   
4              31       Yorkdale-Glen Park       Yorkdale-Glen Park (31)   

      X     Y  LONGITUDE   LATITUDE  OBJECTID   Shape__Area  Shape__Length  \
0  None  None -79.425515  43.676919  16491505  3.217960e+06    7515.779658   
1  None  None -79.403590  43.704689  16491521  3.160334e+06    7872.021074   
2  None  None -79.397871  43.687859  16491537  2.222464e+06    8130.411276   
3  None  None -79.488883  43.765736  16491553  2.541821e+07   25632.335242   
4  None  None -79.457108  43.714672  16491569  1.156669e+07   13953.408098   

                                            geometry  
0  POLYGON ((-79.43592 43.68015, -79.43492 43.680...  
1  POLYGON ((-79.41096 43.70408, -79.40962 43.704...  
2  POLYGON ((-79.39119 43.68108, -79.39141 43.680...  
3  POLYGON ((-79.50529 43.75987, -79.50488 43.759...  
4  POLYGON ((-79.43969 43.70561, -79.44011 43.705...

From the census data I will use the total population and the population over 65 years

In [20]:
toronto_census.head(15)

_id                   Category                      Topic  \
0     1  Neighbourhood Information  Neighbourhood Information   
1     2  Neighbourhood Information  Neighbourhood Information   
2     3                 Population   Population and dwellings   
3     4                 Population   Population and dwellings   
4     5                 Population   Population and dwellings   
5     6                 Population   Population and dwellings   
6     7                 Population   Population and dwellings   
7     8                 Population   Population and dwellings   
8     9                 Population   Population and dwellings   
9    10                 Population        Age characteristics   
10   11                 Population        Age characteristics   
11   12                 Population        Age characteristics   
12   13                 Population        Age characteristics   
13   14                 Population        Age characteristics   
14   15                 Population        Age characteristics   

                       Data Source  \
0                  City of Toronto   
1                  City of Toronto   
2   Census Profile 98-316-X2016001   
3   Census Profile 98-316-X2016001   
4   Census Profile 98-316-X2016001   
5   Census Profile 98-316-X2016001   
6   Census Profile 98-316-X2016001   
7   Census Profile 98-316-X2016001   
8   Census Profile 98-316-X2016001   
9   Census Profile 98-316-X2016001   
10  Census Profile 98-316-X2016001   
11  Census Profile 98-316-X2016001   
12  Census Profile 98-316-X2016001   
13  Census Profile 98-316-X2016001   
14  Census Profile 98-316-X2016001   

                                   Characteristic City of Toronto  \
0                            Neighbourhood Number             NaN   
1                            TSNS2020 Designation             NaN   
2                                Population, 2016       2,731,571   
3                                Population, 2011       2,615,060   
4                     Population Change 2011-2016           4.50%   
5                         Total private dwellings       1,179,057   
6   Private dwellings occupied by usual residents       1,112,929   
7         Population density per square kilometre           4,334   
8                  Land area in square kilometres           630.2   
9                           Children (0-14 years)         398,135   
10                            Youth (15-24 years)         340,270   
11                      Working Age (25-54 years)       1,229,555   
12                   Pre-retirement (55-64 years)         336,670   
13                            Seniors (65+ years)         426,945   
14                      Older Seniors (85+ years)          66,000   

   Agincourt North Agincourt South-Malvern West       Alderwood  \
0              129                          128              20   
1   No Designation               No Designation  No Designation   
2           29,113                       23,757          12,054   
3           30,279                       21,988          11,904   
4           -3.90%                        8.00%           1.30%   
5            9,371                        8,535           4,732   
6            9,120                        8,136           4,616   
7            3,929                        3,034           2,435   
8             7.41                         7.83            4.95   
9            3,840                        3,075           1,760   
10           3,705                        3,360           1,235   
11          11,305                        9,965           5,220   
12           4,230                        3,265           1,825   
13           6,045                        4,105           2,015   
14             925                          555             320   

             Annex  ... Willowdale West Willowridge-Martingrove-Richview  \
0               95  ...              37                                7   
1   No Designation  ... 

In [21]:
toronto_er = toronto_er.merge(toronto_hoods[['_id', 'AREA_NAME']], left_on='Neighborhood', right_on='AREA_NAME')
toronto_er.drop('AREA_NAME', axis=1, inplace=True)
toronto_er.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0     Wychwood              43.676919              -79.425515   
1     Wychwood              43.676919              -79.425515   
2     Wychwood              43.676919              -79.425515   
3     Wychwood              43.676919              -79.425515   
4     Wychwood              43.676919              -79.425515   

                                     Venue  Venue Latitude  Venue Longitude  \
0                   St. Michael's Hospital       43.653784       -79.377809   
1  Toronto General Hospital Emergency Room       43.658426       -79.386462   
2         Mount Sinai Emergency Department       43.656680       -79.390283   
3                     Emergency Department       43.658314       -79.386985   
4                      Sick Kids Emergency       43.657527       -79.386513   

   Venue Category   _id  
0        Hospital  7001  
1  Emergency Room  7001  
2  Emergency Room  7001  
3  Emergency Room  7001  
4  Emergency Room  7001

In [22]:
hood_pop = pd.DataFrame()
hood_pop['_id'] = toronto_census.iloc[0, 6:].astype(int) + 7000
hood_pop['Population'] = toronto_census.iloc[2, 6:].str.replace(',','').astype(int)
hood_pop['Senior Population'] = toronto_census.iloc[13, 6:].str.replace(',','').astype(int) + toronto_census.iloc[14, 6:].str.replace(',','').astype(int)
hood_pop.head()

_id  Population  Senior Population
Agincourt North               7129       29113               6970
Agincourt South-Malvern West  7128       23757               4660
Alderwood                     7020       12054               2335
Annex                         7095       30526               6950
Banbury-Don Mills             7042       27695               8615

In [23]:
bbox = [43.580253, -79.639273, 43.8555442, -79.113219] 
bbox_string = '_'.join([str(x) for x in bbox])
net_filename = 'data/network_{}.h5'.format(bbox_string)
network = osm.pdna_network_from_bbox(bbox[0], bbox[1], bbox[2], bbox[3], network_type='drive')

Requesting network data within bounding box from Overpass API in 1 request(s)
Posting to http://www.overpass-api.de/api/interpreter with timeout=180, "{'data': '[out:json][timeout:180];(way["highway"]["highway"!~"cycleway|footway|path|pedestrian|steps|track|proposed|construction|bridleway|abandoned|platform|raceway|service"]["motor_vehicle"!~"no"]["motorcar"!~"no"]["service"!~"parking|parking_aisle|driveway|emergency_access"](43.58025300,-79.63927300,43.85554420,-79.11321900);>;);out;'}"
Downloaded 42,276.9KB from www.overpass-api.de in 5.27 seconds
Downloaded OSM network data within bounding box from Overpass API in 1 request(s) and 6.36 seconds
Returning OSM data with 250,134 nodes and 49,296 ways...
Edge node pairs completed. Took 97.60 seconds
Returning processed graph with 42,535 nodes and 60,632 edges...
Completed OSM data download and Pandana node and edge table creation in 110.62 seconds


In [24]:
#network.save_hdf5('toronto_network_drive.h5')

In [25]:
#network = Network.from_hdf5('toronto_network.h5')

In [26]:
network.init_pois(num_categories=2, max_dist=5000, max_pois=100)
network.set_pois(category='Hospitals', x_col=toronto_er['Venue Longitude'], y_col=toronto_er['Venue Latitude'])

Reading parameters from init_pois()
Reading parameters from init_pois()


In [27]:
network.set_pois(category='Neighborhood', x_col=toronto_er['Neighborhood Longitude'], y_col=toronto_er['Neighborhood Latitude'])

Reading parameters from init_pois()
Reading parameters from init_pois()


In [28]:
hospitals_nodes = network.get_node_ids(x_col=toronto_er['Venue Longitude'], y_col=toronto_er['Venue Latitude'])
neighborhood_nodes = network.get_node_ids(x_col=toronto_hoods['LONGITUDE'], y_col=toronto_hoods['LATITUDE'])

In [29]:
neighborhood_nodes.count()

140

In [30]:
# Calculate distances between the neighborhoods and the ER Venues
distances = {}
for n_node in neighborhood_nodes:
    distance = []
    for h_node in hospitals_nodes:
        distance.append(network.shortest_path_length(n_node, h_node))
    distances[n_node] = distance

In [31]:
distances_df = pd.DataFrame.from_dict(distances, orient='index', columns = toronto_er['Venue'])
distances_df.reset_index(inplace=True)
distances_df.rename(columns={'index':'node_id'}, inplace=True)
distances_df.set_index(toronto_hoods['_id'], inplace=True)
distances_df = distances_df.merge(hood_pop[['_id', 'Population']], on='_id')
distances_df.head()

_id   node_id  St. Michael's Hospital  \
0  7001  70119690                5911.197   
1  7002  98465008                6459.230   
2  7003  98500099                4437.657   
3  7004  48498586               17861.247   
4  7005  21631765               10931.604   

   Toronto General Hospital Emergency Room  Mount Sinai Emergency Department  \
0                                 4921.257                          4869.351   
1                                 5937.502                          6078.926   
2                                 3770.705                          3912.129   
3                                16871.307                         16819.401   
4                                 9941.664                          9889.758   

   Emergency Department  Sick Kids Emergency  Brynnikins  \
0              4921.257             4970.595    4359.431   
1              5937.502             5986.840    9300.233   
2              3770.705             3820.043    7136.094   
3             16871.307            16920.645   15652.794   
4              9941.664             9991.002    7904.258   

   Princess Margaret Hospital- REACH Clinic  \
0                                  4749.212   
1                                  5765.457   
2                                  3598.660   
3                                 16699.262   
4                                  9769.619   

   Sunnybrook Health Sciences Centre  ...  \
0                           8243.304  ...   
1                           3332.659  ...   
2                           5280.624  ...   
3                          12868.477  ...   
4                           6586.039  ...   

   North York General Hospital - Branson Site  North York General Hospital  \
0                                   11930.868                    14498.780   
1                                    9675.340                     9945.355   
2                                   11522.413                    11929.959   
3                                    3655.185                    11844.640   
4                                    8240.126                    10938.643   

   Emergency Toronto East General Hopital  \
0                                9694.812   
1                                7921.506   
2                                7547.301   
3                               19694.324   
4                               12976.366   

   Peel Paramedic Union Tedlo Station (Region of Peel Paramedics)  \
0                                          19729.613                
1                                          23541.254                
2                                          21768.100                
3                                          26280.362                
4                                          21530.967                

   Trillium Medical Care  Centenary Hospital Emergency  \
0              17311.772                     25184.483   
1              21218.906                     20557.601   
2              19445.752                     22221.803   
3              24023.191                     25581.882   
4              19208.619                     23667.144   

   The Scarborough Hospital - Birchmount Campus  First Aid Zone  \
0                                     21721.929       23791.217   
1                                     17095.047       19296.441   
2                                     18759.249       21281.045   
3                                     15891.769       17219.819   
4                                     18230.786       20231.549   

   Scarborough General Hospital Emergency  Population  
0                               19587.707       33312  
1                               14960.825       32954  
2                               16625.027       10360  
3                               23192.235       10529  
4                               18514.986        9456  

[5 rows x 22 columns]

### 2SFCA

In [32]:
#Function to calculate 2SFCA

def two_sfca(df, er_supply, pop, d0=5000):
    #first step
    er_lst = df.columns.to_list()[2:-1]
    R_dict = {}
    for er in er_lst:
        R_dict[er] = er_supply[er]/(df[df[er]<d0][pop].sum())
    R = pd.DataFrame.from_dict(R_dict, orient='index', columns=['R'])
    #second step
    hood_lst = df._id
    access_dict = {}
    i=0
    dfT = df.iloc[:,2:-1].T 
    for hood in hood_lst:
        access_dict[hood] = R.loc[dfT[dfT[i]<d0].index,'R'].sum()
        i += 1
    access = pd.DataFrame.from_dict(access_dict, orient='index', columns=['Access']).reset_index()
    access.columns = ['_id', 'Access']
    
    return(access)

For this project I will assume a constant er_supply of 100 for all venues

In [33]:
er_supply = {x:100 for x in distances_df.columns.to_list()[2:-1]}
access_all_pop = two_sfca(distances_df, er_supply, 'Population', d0=10000)

In [34]:
#access_all_pop = access_all_pop.merge(toronto_hoods[['_id', 'AREA_NAME']], on='_id')
access_all_pop

_id    Access
0    7001  0.000985
1    7002  0.001265
2    7003  0.000985
3    7004  0.000141
4    7005  0.000837
5    7006  0.000271
6    7007  0.000437
7    7008  0.001173
8    7009  0.001173
9    7010  0.001033
10   7011  0.000730
11   7012  0.000920
12   7013  0.000670
13   7014  0.000389
14   7015  0.000920
15   7016  0.001114
16   7017  0.001012
17   7018  0.000448
18   7019  0.000985
19   7020  0.000092
20   7021  0.000000
21   7022  0.001033
22   7023  0.001124
23   7024  0.001012
24   7025  0.001102
25   7026  0.000280
26   7027  0.000730
27   7028  0.000985
28   7029  0.000985
29   7030  0.000980
..    ...       ...
110  7111  0.000092
111  7112  0.000547
112  7113  0.000000
113  7114  0.001070
114  7115  0.000920
115  7116  0.000920
116  7117  0.001211
117  7118  0.001126
118  7119  0.001126
119  7120  0.000141
120  7121  0.000985
121  7122  0.000448
122  7123  0.000962
123  7124  0.000633
124  7125  0.000633
125  7126  0.000448
126  7127  0.000945
127  7128  0.000000
128  7129  0.000141
129  7130  0.000141
130  7131  0.001126
131  7132  0.000768
132  7133  0.000920
133  7134  0.000633
134  7135  0.000697
135  7136  0.000498
136  7137  0.000985
137  7138  0.000000
138  7139  0.000494
139  7140  0.000983

[140 rows x 2 columns]

In [35]:
toronto_er_all_pop = choropleth_map(loc=toronto_coord, geodata = 'Neighbourhoods.geojson', data=access_all_pop, cols=['_id', 'Access'], legend="ER Access per Neighborhood")

In [36]:
toronto_er_all_pop

In [37]:
distances_df.drop('Population', inplace=True, axis=1)
distances_df = distances_df.merge(hood_pop[['_id', 'Senior Population']], on='_id')
distances_df.head()

_id   node_id  St. Michael's Hospital  \
0  7001  70119690                5911.197   
1  7002  98465008                6459.230   
2  7003  98500099                4437.657   
3  7004  48498586               17861.247   
4  7005  21631765               10931.604   

   Toronto General Hospital Emergency Room  Mount Sinai Emergency Department  \
0                                 4921.257                          4869.351   
1                                 5937.502                          6078.926   
2                                 3770.705                          3912.129   
3                                16871.307                         16819.401   
4                                 9941.664                          9889.758   

   Emergency Department  Sick Kids Emergency  Brynnikins  \
0              4921.257             4970.595    4359.431   
1              5937.502             5986.840    9300.233   
2              3770.705             3820.043    7136.094   
3             16871.307            16920.645   15652.794   
4              9941.664             9991.002    7904.258   

   Princess Margaret Hospital- REACH Clinic  \
0                                  4749.212   
1                                  5765.457   
2                                  3598.660   
3                                 16699.262   
4                                  9769.619   

   Sunnybrook Health Sciences Centre  ...  \
0                           8243.304  ...   
1                           3332.659  ...   
2                           5280.624  ...   
3                          12868.477  ...   
4                           6586.039  ...   

   North York General Hospital - Branson Site  North York General Hospital  \
0                                   11930.868                    14498.780   
1                                    9675.340                     9945.355   
2                                   11522.413                    11929.959   
3                                    3655.185                    11844.640   
4                                    8240.126                    10938.643   

   Emergency Toronto East General Hopital  \
0                                9694.812   
1                                7921.506   
2                                7547.301   
3                               19694.324   
4                               12976.366   

   Peel Paramedic Union Tedlo Station (Region of Peel Paramedics)  \
0                                          19729.613                
1                                          23541.254                
2                                          21768.100                
3                                          26280.362                
4                                          21530.967                

   Trillium Medical Care  Centenary Hospital Emergency  \
0              17311.772                     25184.483   
1              21218.906                     20557.601   
2              19445.752                     22221.803   
3              24023.191                     25581.882   
4              19208.619                     23667.144   

   The Scarborough Hospital - Birchmount Campus  First Aid Zone  \
0                                     21721.929       23791.217   
1                                     17095.047       19296.441   
2                                     18759.249       21281.045   
3                                     15891.769       17219.819   
4                                     18230.786       20231.549   

   Scarborough General Hospital Emergency  Senior Population  
0                               19587.707               5595  
1                               14960.825               3860  
2                               16625.027               2230  
3                               23192.235               2030  
4                               18514.986               1420  

[5 rows x 22 columns]

In [38]:
er_supply = {x:33 for x in distances_df.columns.to_list()[2:-1]}
access_senior_pop = two_sfca(distances_df, er_supply, pop = 'Senior Population', d0=0000)

D:\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: RuntimeWarning: divide by zero encountered in longlong_scalars
  


In [39]:
toronto_er_senior_pop = choropleth_map(loc=toronto_coord, geodata = 'Neighbourhoods.geojson', data=access_all_pop, cols=['_id', 'Access'], legend="ER per Neighborhood for Senior Population")

In [40]:
toronto_er_senior_pop

## Notes:

[1] Universal health coverage and universal access, Bulletin of the World Health Organization 2013; 91:546–546A

[2] McGrail MR. Spatial accessibility of primary health care utilising the two step floating catchment area method: an assessment of recent improvements. Int J Health Geogr. 2015;11:50.

[3] https://collections.ola.org/mon/30011/337443.pdf